# Introduction to latttice-based encryption

## LWE encryption

We first recall basic lattice-based encryption, starting from the Regev scheme [Reg05].

Let $q \in {\mathbb Z}$ be a prime number. Let $\vec{s} \in {\mathbb Z}^n$ be the secret-key. 
An LWE ciphertext for a message $m \in \{0,1\}$ is a vector $\vec{c} \in {\mathbb F}_q^n$ such that
$$ \langle \vec{c},\vec{s} \rangle= e + m \cdot \lfloor q/2 \rceil \pmod{q}$$
where for the error $e$, we can take the centered binomial distribution $\chi$ with
parameter $\kappa$. 

One can let $e=h(u)-h(v)$
where $u,v \leftarrow \{0,1\}^\kappa$, where $h$ is the Hamming weight function.

In [ ]:
def hw(x):
  return sum(x.digits(base=2))

def binom(kappa=2):
  return hw(ZZ.random_element(2^kappa))-hw(ZZ.random_element(2^kappa))

For simplicity, we first consider the symmetric scheme. We consider a binary secret-key $\vec{s}=(s_1,\cdots,s_n)$, with $s_1=1$.

In [ ]:
def genKey(n=10,kappa=2,nq=6):
  q=next_prime(2^nq)
  s=vector(ZZ,[1]+[ZZ.random_element(2) for i in range(n-1)])
  return kappa,q,s

In [ ]:
kappa,q,s=genKey()
"kappa=%d, q=%d, s=%s" % (kappa,q,s.__str__())

An LWE ciphertext is a vector of elements in ${\mathbb Z}_q$. We have taken $s_1=1$, so 
$$\langle \vec{c},\vec{s} \rangle = c_1 + \sum\limits_{i=2}^n c_i \cdot s_i = e + m \cdot \lfloor q/2 \rceil \pmod{q}$$

In [ ]:
def LWEencSym(mes,q,kappa,s):
  a=vector(GF(q),[ZZ.random_element(q) for j in range(s.length())])
  a[0]=-a[1:]*s[1:]+binom(kappa)+ZZ((q-1)/2)*mes
  return a

Decryption is performed by computing
$m={\sf th}(\langle \vec{c},\vec{s} \rangle \bmod q)$, where ${\sf th}(x)=1$ if $q/4 \leq x \leq 3q/4$, and $0$ otherwise.

In [ ]:
def th(x,q):
  if x>=q/4 and x<3*q/4: return 1
  return 0

def LWEdecrypt(c,q,s):
  return th((c*s).lift(),q)

To encrypt from the public-key, one can use a matrix 
${\bf A} \in {\mathbb F}_q^{\ell \times n}$ of row vectors  ${\vec a}_i \in {\mathbb F}_q^n$, such that 
$$ \langle \vec{a}_i,\vec{s} \rangle= e_i \pmod q$$
for $e_i \leftarrow \chi$, for all $1 \leq i \leq \ell$.

This can be written ${\bf A} \cdot \vec{s}= \vec{e} \pmod{q}$.
Therefore, every row of $\vec{A}$ is an LWE encryption of $0$.

In [ ]:
def vecBinom(n,kappa=2):
  return vector([binom(kappa) for i in range(n)])

def genKeyPK(n=10,ell=40,kappa=2,nq=6):
  q=next_prime(2^nq)
  A=Matrix(GF(q),[[ZZ.random_element(q) for j in range(n)] for i in range(ell)])
  s=vector(ZZ,[1]+[ZZ.random_element(2) for i in range(n-1)])
  A[:,0]=-A[:,1:]*s[1:]+vecBinom(ell,kappa)
  return kappa,q,A,s

In [ ]:
kappa,q,A,s=genKeyPK()

To encrypt a  message $m \in \{0,1\}$, one generates a linear
combination of the row vectors ${\vec a}_i$: 
\begin{align*}
\vec{c}  =\left\lfloor \frac{q}{2} \right\rceil \cdot
(m,0,\ldots,0)+ \vec{u} \cdot \vec{A} \pmod q 
\end{align*}
where $\vec{u} \leftarrow \chi^\ell$.

In [ ]:
def LWEenc(mes,A,kappa,q):
    pass

def testLWE():
    pass

## RLWE encryption

For RLWE encryption, we replace ${\mathbb Z}_q$ by 
the polynomial ring $R_q={\mathbb Z}_q[x] / <x^k+1>$, where $k$
is a power of $2$. 

 Addition and multiplication of polynomials are performed modulo
  $x^k+1$ and prime $q$.
 We can take $m \in R_2={\mathbb Z}_2[x] / <\!x^k+1\!>$.

In [ ]:
def genRings(k=8,nq=6):
  R=ZZ['x']
  p=R.gen()^k+1
  q=next_prime(2^nq)
  Rq=R.change_ring(GF(q))
  return R,k,p,q,Rq

R,k,p,q,Rq=genRings()

The public-key is $(a,t)$ with $t=a \cdot s+e$
for random $a$ in $R_q$ and small $s$, $e$ in $R$.

In [ ]:
def binomialRLWE(R,k,kappa):
  return R([binom(kappa) for i in range(k)])

def genKeyRLWE(kappa=2,k=8,nq=6):
  R,k,p,q,Rq=genRings(k,nq)
  s=binomialRLWE(R,k,kappa)
  a=Rq([ZZ.random_element(q) for i in range(k)])
  e=binomialRLWE(R,k,kappa)
  t=(a*s+e) % p
  return q,Rq,R,p,kappa,k,a,t,s

In [ ]:
q,Rq,R,p,kappa,k,a,t,s=genKeyRLWE()

To encrypt
a message $m \in R_2$, compute
$ c=(a \cdot r+e_1,~t \cdot r+e_2 + \lfloor q/2 \rceil m)$,
for small $e_1$, $e_2$ and $r$ in $R$. 

To decrypt,
compute $m={\sf th}(v- s \cdot u)$.
\begin{align*}
 v- { s} \cdot u & =
     { t} \cdot r+e_2 + \lfloor q/2 \rceil m
     - { s} \cdot ( { a} \cdot
     r+e_1) \\
     & = ({ t} -{ a}
     \cdot { s} ) \cdot r+e_2 + \lfloor q/2 \rceil m
     - { s} \cdot e_1 \\
     & =\lfloor q/2 \rceil m +
\underbrace{
     { e} \cdot  r + e_2
     - { s} \cdot e_1}_{\text{small}}
\end{align*}

In [ ]:
def encryptRLWE(m,R,q,p,kappa,k,a,t):
  pass

def decryptRLWE(c,R,q,p,s):
  pass

def testRLWE():
  pass

The error $e$ must be kept secret, otherwise we can recover the secret-key $s$ using
$$ s=(t-e)/a \pmod{x^k+1,q}$$

In [ ]:
def from_e():
    s=binomialRLWE(R,k,kappa)
    print("s= %s" % str(s))
    a=Rq([ZZ.random_element(q) for i in range(k)])
    e=binomialRLWE(R,k,kappa)
    t=(a*s+e) % p
    
    # show how to recover s from the knowledge of a, t and e.
    pass

## Tasks
1. Write the LWE public-key encryption function
2. Write the RLWE public-key encryption and decryption functions.
3. Write the attack recovering the secret $s$ from the knowledge of $a$, $t$ and $e$.